# Notebook for replicating the analyses in "How does a Move to a Flat Tax Affect Montana Household Filers?"
### Richard W. Evans and Paul Johnston, April 2024
This notebook replicates the analyses in the *Research in Focus* article by [Richard W. Evans](https://sites.google.com/site/rickecon) and Paul Johnston entitled "How does a Move to a Flat Tax Affect Montana Household Filers?".

This Jupyter notebook is meant for execution on your local machine and is located at https://github.com/TheCGO/MT-FlatTax/blob/main/MT_FlatTax.ipynb.

## 0. Setting up the environment
To set up the environment:
1. Update your local clone of the `fiscalsim-us` repository on your machine
    * If you don't have the `fiscalsim-us` repository cloned on your machine:
        * Create a fork of the FiscalSim-US main repository (https://github.com/TheCGO/fiscalsim-us) to your GitHub account
        * Navigate to the directory in your terminal where you want to save this repository
        * Clone that fork onto your local machine: `git clone https://github.com/[YourGitHubHandle]/fiscalsim-us.git`
        * Change directory to the new `fiscalsim-us` directory: `cd fiscalsim-us`
        * Create an `upstream` remote that points to the main repository: `git remote add upstream https://github.com/thecgo/fiscalsim-us.git`
    * If you already have the `fiscalsim-us` repository cloned on your machine:
        * Navigate to your `fiscalsim-us` repository directory in your terminal.
        * Make sure you have an `upstream` remote that points to the main `fiscalsim-us` directory
        * Make sure your main branch is updated with the most current changes in the fiscalsim-us `main` directory: `git fetch upstream`
        * Merge those changes into your `main` directory: `git merge upstream/main`
        * Push those changes out to your remote fork: `git push origin main`
2. Create a new branch called `rickecon-pe06220` that comes from Rick's `pe06220` branch
    * Create a new branch called `rickecon-pe06220`: `git checkout -b rickecon-pe06220 main`
    * Pull the changes from Rick's branch into this new branch of your local fork: `git pull https://github.com/rickecon/fiscalsim-us.git pe06220`
3. Create a new conda environment from this `rickecon-pe06220` branch called `fiscalsim-us-dev2`
    * Navigate to the `fiscalsim-us` repository directory in your terminal on your local machine
    * Create the base of the conda environment using the `environment.yml` file in this repository: `conda env create -f environment.yml`
    * Activate the new conda environment: `conda activate fiscalsim-us-dev2`
    * Install fiscalsim-us package directly from this repository's `setup.py` file.
        * For Linux: `pip install -e .[dev]`
        * For Mac: `pip install -e ."[dev]"`
        * For Windows: `pip install -e .'[dev]'`

In your new branch `rickecon-pe06220`, with the new conda environment `fiscalsim-us-dev2` activated, you should be able to run all the analyses below.

### 1. Introduction
Before opening and running this notebook, make sure that you have downloaded or cloned the KS-FlatTax repository (https://github.com/TheCGO/KS-FlatTax) and created and activated the associated conda environment ks-flattax-dev in the environment.yml file.

The notebook for the introduction produces the following figures.

* 1.1. Figure 1. Plot of US states by state employment income tax type

In [1]:
# Import packages (this might take a little more than a minute)
import pandas as pd
import numpy as np
import geopandas as gpd
from bokeh.io import output_file, output_notebook, export_png
from bokeh.plotting import figure, show
from bokeh.models import (ColumnDataSource, Title, Label, LabelSet, Legend,
                          LegendItem, CategoricalColorMapper, ColorBar,
                          HoverTool, NumeralTickFormatter, GeoJSONDataSource,
                          FactorRange)
from bokeh.models.tickers import SingleIntervalTicker
from bokeh.transform import factor_cmap
from bokeh.sampledata.us_states import data as states
from bokeh.palettes import Category10

import random
import json

from fiscalsim_us.model_api import *
from fiscalsim_us import Simulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant

### 3. Effects of the flat tax reform on Montana tax filers
#### 3.1. Define the 12 filer types
These 12 filer types are detailed in Appendix C of the paper.

#### 3.1.1 Define the three single filer types
Single, no kids, low income (household before-tax income = $13,000)

In [2]:
situation_sgl_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "13000"},
            "medical_out_of_pocket_expenses": {"2024": "200"},
        },
    },
    "families": {
        "your family": {
            "members": [
                "you",
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
            ],
            "broadband_cost": {"2024": "400"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "5000"},
            "phone_cost": {"2024": "500"},
            "spm_unit_id": {"2024": "0"},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Single no kids, middle income (household before-tax income = $40,000)


In [3]:
situation_sgl_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "employment_income": {"2024": "40000"},
            "medical_out_of_pocket_expenses": {"2024": "1000"},
        },
    },
    "families": {
        "your family": {
            "members": [
                "you",
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
            ],
            "broadband_cost": {"2024": "700"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "15000"},
            "phone_cost": {"2024": "1200"},
            "spm_unit_id": {"2024": "0"},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Single, no kids, high income (household before-tax income = $90,000)

In [4]:
situation_sgl_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "8000"},
            "employment_income": {"2024": "90000"},
            "medical_out_of_pocket_expenses": {"2024": "2000"},
        },
    },
    "families": {
        "your family": {
            "members": [
                "you",
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "30000"},
            "phone_cost": {"2024": "2000"},
            "spm_unit_id": {"2024": "0"},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

#### 3.1.2 Define the three head of household filer types
Head of household, 2 kids, low income (household before-tax income = $18,000)

In [5]:
situation_hoh_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "20000"},
            "medical_out_of_pocket_expenses": {"2024": "500"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "1000"},
            "housing_cost": {"2024": "9000"},
            "phone_cost": {"2024": "600"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Head of household, 2 kids, middle income (household before-tax income = $60,000)

In [6]:
situation_hoh_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "employment_income": {"2024": "60000"},
            "medical_out_of_pocket_expenses": {"2024": "2000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "2000"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Head of household, 2 kids, high income (household before-tax income = $150,000)

In [7]:
situation_hoh_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "15000"},
            "employment_income": {"2024": "150000"},
            "medical_out_of_pocket_expenses": {"2024": "3000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "3000"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

#### 3.1.3 Define the six married filing jointly filer types
Married filing jointly, 0 kids, low income (household before-tax income = $22,000)

In [8]:
situation_mar_0_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "12000"},
            "medical_out_of_pocket_expenses": {"2024": "400"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "10000"},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "6000"},
            "phone_cost": {"2024": "800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Married filing jointly, 0 kids, middle income (household before-tax income = $60,000)

In [9]:
situation_mar_0_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "employment_income": {"2024": "35000"},
            "medical_out_of_pocket_expenses": {"2024": "1800"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "25000"},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "18000"},
            "phone_cost": {"2024": "1200"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Married filing jointly, 0 kids, high income (household before-tax income = $160,000)

In [10]:
situation_mar_0_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "16000"},
            "employment_income": {"2024": "90000"},
            "medical_out_of_pocket_expenses": {"2024": "3000"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "70000"},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "2000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Married filing jointly, 2 kids, low income (household before-tax income = $25,000)

In [11]:
situation_mar_2_low = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "0"},
            "employment_income": {"2024": "25000"},
            "medical_out_of_pocket_expenses": {"2024": "600"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "0"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "500"},
            "childcare_expenses": {"2024": "1000"},
            "housing_cost": {"2024": "10000"},
            "phone_cost": {"2024": "800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Married filing jointly, 2 kids, middle income (household before-tax income = $70,000)

In [12]:
situation_mar_2_mid = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "employment_income": {"2024": "40000"},
            "medical_out_of_pocket_expenses": {"2024": "2500"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "30000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "2200"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

Married filing jointly, 2 kids, high income (household before-tax income = $200,000)

In [13]:
situation_mar_2_high = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "20000"},
            "employment_income": {"2024": "100000"},
            "medical_out_of_pocket_expenses": {"2024": "3500"},
        },
        "your partner": {
            "age": {"2024": "35"},
            "employment_income": {"2024": "100000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "1200"},
            "childcare_expenses": {"2024": "3000"},
            "housing_cost": {"2024": "36000"},
            "phone_cost": {"2024": "1800"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    }
}

#### 3.2. Run all baseline and reform simulations

In [14]:
# Create baseline (no change) parameters
def modify_parameters_b(parameters):
    """
    Baseline reform is to not modify the parameters.
    """
    pass
    return parameters



# Create  baseline (no change) reform
class reform_b(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters_b)



# Define the parameters that change in the reform
def modify_parameters_1(parameters):
    # Defining flat tax
    parameters.gov.states.mt.tax.income.rates.joint[0].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    parameters.gov.states.mt.tax.income.rates.joint[1].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    parameters.gov.states.mt.tax.income.rates.head_of_household[0].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    parameters.gov.states.mt.tax.income.rates.head_of_household[1].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    parameters.gov.states.mt.tax.income.rates.separate[0].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    parameters.gov.states.mt.tax.income.rates.separate[1].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    parameters.gov.states.mt.tax.income.rates.single[0].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    parameters.gov.states.mt.tax.income.rates.single[1].rate.update(
        start=instant("2024-01-01"), stop=instant("2028-12-31"), value=0.0515
    )
    # # Increasing the standard deduction rate
    # ?
    # # Increasing the standard deduction max
    # ?

    return parameters


class reform_1(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters_1)


def calculate_base_reform(sim_name, base_reform, reform, situation):
    print("Simulating baseline scenario for:", sim_name)
    simulation_b = Simulation(reform=base_reform, situation=situation)
    simulation_b.trace = True
    income_before_tax = sum(simulation_b.calculate("employment_income", 2024))
    income_after_tax_b = simulation_b.calculate("household_net_income", 2024)[0]
    mt_net_tax_liability_b = simulation_b.calculate("mt_income_tax", 2024)[0]
    print("Simulating reform scenario for:", sim_name)
    simulation_r = Simulation(reform=reform, situation=situation)
    simulation_r.trace = True
    income_after_tax_r = simulation_r.calculate("household_net_income", 2024)[0]
    mt_net_tax_liability_r = simulation_r.calculate("mt_income_tax", 2024)[0]
    mt_net_tax_liab_dol_chg = mt_net_tax_liability_r - mt_net_tax_liability_b
    mt_net_tax_liab_pct_chg = (mt_net_tax_liab_dol_chg /
                               np.absolute(mt_net_tax_liability_b))
    print("")
    return (
        income_before_tax, income_after_tax_b, mt_net_tax_liability_b,
        income_after_tax_r, mt_net_tax_liability_r, mt_net_tax_liab_dol_chg,
        mt_net_tax_liab_pct_chg
    )

simulations = [
    ('Single, no kids, low income', situation_sgl_low),
    ('Single, no kids, middle income', situation_sgl_mid),
    ('Single, no kids, high income', situation_sgl_high),
    ('Married filing jointly, no kids, low income', situation_mar_0_low),
    ('Married filing jointly, no kids, middle income', situation_mar_0_mid),
    ('Married filing jointly, no kids, high income', situation_mar_0_high),
    ('Head of household, 2 kids, low income', situation_hoh_low),
    ('Head of household, 2 kids, middle income', situation_hoh_mid),
    ('Head of household, 2 kids, high income', situation_hoh_high),
    ('Married, 2 kids, low income', situation_mar_2_low),
    ('Married, 2 kids, middle income', situation_mar_2_mid),
    ('Married, 2 kids, high income', situation_mar_2_high),
]

results = []

# Loop through each simulation
for sim_name, situation in simulations:
    # Calculate before_tax_income, after_tax_income, and mt_net_tax_liability
    (income_before_tax, income_after_tax_b, mt_net_tax_liability_b,
     income_after_tax_r, mt_net_tax_liability_r, mt_net_tax_liab_dol_chg,
     mt_net_tax_liab_pct_chg) = calculate_base_reform(sim_name, reform_b,
                                                      reform_1, situation)

    # Append the results as a dictionary where key is the column name and value
    # is the simulation output
    results.append({
        "Situation": sim_name,
        "Before tax income": income_before_tax,
        "Baseline after tax income": income_after_tax_b,
        "Baseline Montana net tax liability": mt_net_tax_liability_b,
        "Reform after tax income": income_after_tax_r,
        "Reform Montana net tax liability": mt_net_tax_liability_r,
        "Montana net tax liability change, dollars": mt_net_tax_liab_dol_chg,
        "Montana net tax liability change, percent": mt_net_tax_liab_pct_chg
    })

# Convert the results to a DataFrame
df = pd.DataFrame(results)

# Check the DataFrame
df


Simulating baseline scenario for: Single, no kids, low income
<140567451944176_-8552477337066760109_is_ssi_aged.is_ssi_aged object at 0x7fd888fc08e0>
<140567451944176_-3312292701830264503_is_blind.is_blind object at 0x7fd848185510>
<140567451944176_-1554425099449217470_is_ssi_disabled.is_ssi_disabled object at 0x7fd888fc0bb0>
<140567451944176_-4059017086769376635_is_ssi_aged_blind_disabled.is_ssi_aged_blind_disabled object at 0x7fd888fc0670>
<140567451944176_-7562301199476161876_ssi_ineligible_child_allocation.ssi_ineligible_child_allocation object at 0x7fd888f87e50>
<140567451944176_-2489935722451967595_ssi_unearned_income.ssi_unearned_income object at 0x7fd888f87ca0>
<140567451944176_-7562301199476161876_ssi_ineligible_child_allocation.ssi_ineligible_child_allocation object at 0x7fd888f87e50>
<140567451944176_-7562301199476161876_ssi_ineligible_child_allocation.ssi_ineligible_child_allocation object at 0x7fd888f87e50>
<140567451944176_-7034015197070362398_snap_normal_allotment.snap_n

Situation  Before tax income  \
0                      Single, no kids, low income            13000.0   
1                   Single, no kids, middle income            40000.0   
2                     Single, no kids, high income            90000.0   
3      Married filing jointly, no kids, low income            22000.0   
4   Married filing jointly, no kids, middle income            60000.0   
5     Married filing jointly, no kids, high income           160000.0   
6            Head of household, 2 kids, low income            20000.0   
7         Head of household, 2 kids, middle income            60000.0   
8           Head of household, 2 kids, high income           150000.0   
9                      Married, 2 kids, low income            25000.0   
10                  Married, 2 kids, middle income            70000.0   
11                    Married, 2 kids, high income           200000.0   

    Baseline after tax income  Baseline Montana net tax liability  \
0                16325.244141                          361.429993   
1                34124.000000                         1653.800049   
2                71474.000000                         4432.109863   
3                26270.625000                          566.820007   
4                52178.000000                         2127.600098   
5               128878.000000                         7684.220215   
6                39633.199219                          345.450012   
7                55569.000000                         2090.709961   
8               121032.000000                         7116.330078   
9                46419.101562                          430.519989   
10               64653.000000                         2397.820068   
11              161618.000000                         9488.440430   

    Reform after tax income  Reform Montana net tax liability  \
0              16325.244141                        396.035004   
1              34124.000000                       1658.300049   
2              71474.000000                       4083.435059   
3              26270.625000                        621.090027   
4              52178.000000                       2286.600098   
5             128878.000000                       7136.870117   
6              39633.199219                        378.524994   
7              55569.000000                       2147.034912   
8             121032.000000                       6533.805176   
9              46419.101562                        471.739990   
10             64653.000000                       2522.469971   
11            161618.000000                       8711.740234   

    Montana net tax liability change, dollars  \
0                                   34.605011   
1                                    4.500000   
2                                 -348.674805   
3                                   54.270020   
4                                  159.000000   
5                                 -547.350098   
6                                   33.074982   
7                                   56.324951   
8                                 -582.524902   
9                                   41.220001   
10                                 124.649902   
11                                -776.700195   

    Montana net tax liability change, percent  
0                                    0.095745  
1                                    0.002721  
2                                   -0.078670  
3                                    0.095745  
4                                    0.074732  
5                                   -0.071230  
6                                    0.095745  
7                                    0.026941  
8                                   -0.081857  
9                                    0.095745  
10                                   0.051985  
11                                  -0.081858

### 3.3. Make plot of Montana net tax liability by before-tax income for 4 filer types

#### 3.3.1. Create the four new filers with employment income allowed to vary

In [15]:
inc_min = 0
inc_max = 200_000
num_points = 10001

Create new Single filer with two children, the same other characteristics as the middle income type, and income varying.

In [16]:
situation_sgl_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "medical_out_of_pocket_expenses": {"2024": "1000"},
        },
    },
    "families": {
        "your family": {
            "members": [
                "you",
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
            ],
            "broadband_cost": {"2024": "700"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "15000"},
            "phone_cost": {"2024": "1200"},
            "spm_unit_id": {"2024": "0"},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}


Create new Married filing jointly filer with no children, the same other characteristics as the middle income type, and income varying.

In [17]:
situation_mar_0_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "medical_out_of_pocket_expenses": {"2024": "1800"},
        },
        "your partner": {
            "age": {"2024": "35"},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "0"},
            "housing_cost": {"2024": "18000"},
            "phone_cost": {"2024": "1200"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}


Create new Head of household filer with two children, the same other characteristics as the middle income type, and income varying.

In [18]:
situation_hoh_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2000"},
            "medical_out_of_pocket_expenses": {"2024": "2000"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "800"},
            "childcare_expenses": {"2024": "2000"},
            "housing_cost": {"2024": "20000"},
            "phone_cost": {"2024": "1000"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}


Create new Married filing jointly filer with two children, the same other characteristics as the middle income type, and income varying.

In [19]:
situation_mar_2_mid_plot = {
    "people": {
        "you": {
            "age": {"2024": "38"},
            "charitable_cash_donations": {"2024": "2500"},
            "medical_out_of_pocket_expenses": {"2024": "2500"},
        },
        "your partner": {
            "age": {"2024": "35"},
        },
        "your first dependent": {
            "age": {"2024": "10"},
            "is_tax_unit_dependent": {"2024": True},
        },
        "your second dependent": {
            "age": {"2024": "6"},
            "is_tax_unit_dependent": {"2024": True},
        }
    },
    "families": {
        "your family": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "marital_units": {
        "your marital unit": {
            "members": ["you", "your partner"],
            "marital_unit_id": {"2024": 0}
        },
        "your first dependent's marital unit": {
            "members": ["your first dependent"],
            "marital_unit_id": {"2024": 2}
        },
        "your second dependent's marital unit": {
            "members": ["your second dependent"],
            "marital_unit_id": {"2024": 3}
        }
    },
    "tax_units": {
        "your tax unit": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ]
        }
    },
    "spm_units": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "broadband_cost": {"2024": "900"},
            "childcare_expenses": {"2024": "2200"},
            "housing_cost": {"2024": "22000"},
            "phone_cost": {"2024": "1500"},
            "spm_unit_id": {"2024": 0},
        }
    },
    "households": {
        "your household": {
            "members": [
                "you",
                "your partner",
                "your first dependent",
                "your second dependent"
            ],
            "state_living_arrangement": {"2024": "FULL_COST"},
            "state_name": {"2024": "MT"}
        }
    },
    "axes": [
        [
            {
                "name": "employment_income",
                "count": num_points,
                "min": inc_min,
                "max": inc_max
            }
        ]
    ]
}


#### 3.3.2. Create the plot of the four filer types varying by income

Create the data series for the four lines of the plot.

In [20]:
def calculate_base_reform_plot(sim_name, base_reform, reform, situation):
    print("Simulating baseline scenario for plot:", sim_name)
    simulation_b = Simulation(reform=base_reform, situation=situation)
    simulation_b.trace = True
    income_before_tax_vec = simulation_b.calculate("employment_income", 2024)
    income_after_tax_b_vec = simulation_b.calculate("household_net_income",
                                                    2024)
    mt_net_tax_liability_b_vec = simulation_b.calculate("mt_income_tax", 2024)
    print("Simulating reform scenario for plot:", sim_name)
    simulation_r = Simulation(reform=reform, situation=situation)
    simulation_r.trace = True
    income_after_tax_r_vec = simulation_r.calculate("household_net_income",
                                                    2024)
    mt_net_tax_liability_r_vec = simulation_r.calculate("mt_income_tax", 2024)
    mt_net_tax_liab_dol_chg_vec = (mt_net_tax_liability_r_vec -
                                   mt_net_tax_liability_b_vec)
    mt_net_tax_liab_pct_chg_vec = (mt_net_tax_liab_dol_chg_vec /
                                   np.absolute(mt_net_tax_liability_b_vec))
    print("")
    return (
        income_before_tax_vec, income_after_tax_b_vec,
        mt_net_tax_liability_b_vec, income_after_tax_r_vec,
        mt_net_tax_liability_r_vec, mt_net_tax_liab_dol_chg_vec,
        mt_net_tax_liab_pct_chg_vec
    )

results_plot = []
df_list = []
cds_list = []
filer_type_label_list = []

sims_to_plot = [
    ('Single, no kids', situation_sgl_mid_plot),
    ('Married filing jointly, no kids', situation_mar_0_mid_plot),
    ('Head of household, 2 kids', situation_hoh_mid_plot),
    ('Married filing jointly, 2 kids', situation_mar_2_mid_plot)
]

# Loop through each simulation with varying income
for sim_name, situation in sims_to_plot:
    # Calculate before_tax_income, after_tax_income, and ks_net_tax_liability
    (inc_before_tax_vec, inc_after_tax_b_vec, mt_net_tax_liab_b_vec,
     inc_after_tax_r_vec, mt_net_tax_liab_r_vec,
     mt_net_tax_liab_dol_chg_vec, mt_net_tax_liab_pct_chg_vec) = \
        calculate_base_reform_plot(sim_name, reform_b, reform_1, situation)
    if sim_name == "Head of household, 2 kids":
        inc_before_tax_vec_weird = inc_before_tax_vec.copy()

    # Create a DataFrame
    data_df = pd.DataFrame([])
    if sim_name == "Single, no kids":
        data_df["inc_before_tax"] = inc_before_tax_vec
    elif sim_name == "Married filing jointly, no kids":
        # Income before tax array gives incomes for both spouses for Married
        # filing jointly, no kids. Take only even indices 0, 2, 4,... .
        data_df["inc_before_tax"] = inc_before_tax_vec[0::2]
    elif sim_name == "Head of household, 2 kids":
        # Income before tax array gives incomes for head of household and for
        # both children for Head of household, 2 kids. Take only every third
        # index 0, 3, 6,... .
        data_df["inc_before_tax"] = inc_before_tax_vec[0::3]
    elif sim_name == "Married filing jointly, 2 kids":
        # Income before tax array gives incomes for both spouses and for both
        # children for Married filing jointly, 2 kids. Take only every fourth
        # index 0, 4, 8,... .
        data_df["inc_before_tax"] = inc_before_tax_vec[0::4]
    data_df["inc_after_tax_b"] = inc_after_tax_b_vec
    data_df["mt_net_tax_liab_b"] = mt_net_tax_liab_b_vec
    data_df["inc_after_tax_r"] = inc_after_tax_r_vec
    data_df["mt_net_tax_liab_r"] = mt_net_tax_liab_r_vec
    data_df["mt_net_tax_liab_dol_chg"] = mt_net_tax_liab_dol_chg_vec
    data_df["mt_net_tax_liab_pct_chg"] = mt_net_tax_liab_pct_chg_vec
    data_df["filer_type"] = sim_name

    # Append the sim name to the filer_type_label_list
    filer_type_label_list.append(sim_name)

    # Append the results as a dictionary where key is the column name and value
    # is the simulation output
    results_plot.append({
        "Situation": sim_name,
        "Before tax income vector": inc_before_tax_vec,
        "Baseline Montana net tax liability vector": mt_net_tax_liab_b_vec,
        "Reform Montana net tax liability vector": mt_net_tax_liab_r_vec,
        "Montana net tax liability change vector, dollars": mt_net_tax_liab_dol_chg_vec,
        "Pandas DataFrame": data_df
    })

    # Append the data_df as a Pandas DataFrame object to the df_list
    df_list.append(data_df)

    # Append the data_df as a ColumnDataSource object to the cds_list
    cds_list.append(ColumnDataSource(data_df))


Simulating baseline scenario for plot: Single, no kids
<140567451956656_-8552477337066760109_is_ssi_aged.is_ssi_aged object at 0x7fd88c3efd30>
<140567451956656_-3312292701830264503_is_blind.is_blind object at 0x7fd88a6849a0>
<140567451956656_-1554425099449217470_is_ssi_disabled.is_ssi_disabled object at 0x7fd88c35c070>
<140567451956656_-4059017086769376635_is_ssi_aged_blind_disabled.is_ssi_aged_blind_disabled object at 0x7fd88c3efac0>
<140567451956656_-7562301199476161876_ssi_ineligible_child_allocation.ssi_ineligible_child_allocation object at 0x7fd88c3ef2e0>
<140567451956656_-2489935722451967595_ssi_unearned_income.ssi_unearned_income object at 0x7fd88c3ef130>
<140567451956656_-7562301199476161876_ssi_ineligible_child_allocation.ssi_ineligible_child_allocation object at 0x7fd88c3ef2e0>
<140567451956656_-7562301199476161876_ssi_ineligible_child_allocation.ssi_ineligible_child_allocation object at 0x7fd88c3ef2e0>
<140567451956656_-7034015197070362398_snap_normal_allotment.snap_normal_a

In [21]:
# Save source data for figure 4
fig4_source_df = df_list[0][["inc_before_tax", "mt_net_tax_liab_dol_chg"]].rename(columns={"mt_net_tax_liab_dol_chg": "mt_net_tax_liab_dol_chg_single"})
fig4_source_df["mt_net_tax_liab_dol_chg_mar0kids"] = df_list[1]["mt_net_tax_liab_dol_chg"]
fig4_source_df["mt_net_tax_liab_dol_chg_hoh2kids"] = df_list[2]["mt_net_tax_liab_dol_chg"]
fig4_source_df["mt_net_tax_liab_dol_chg_mar2kids"] = df_list[3]["mt_net_tax_liab_dol_chg"]
fig4_source_df.to_csv('./data/fig4_source.csv', index=False)

OSError: Cannot save file into a non-existent directory: 'data'

Create the Bokeh plot for Figure 4.

In [23]:
# Create Bokeh plot of Figure 4 change in Montana net tax liability
# fig4_title = ("Dollar change from Montana flat tax reform in filer net state " +
#              "income tax liability")
fig4_title = ""
filename4 = "./images/NetStateTaxLiabChg.html"
output_file(filename4, title=fig4_title, mode='inline')
output_notebook()

# Format the tooltip
tooltips = [
    ("Filer type", "@filer_type"),
    ("Before-tax employment income", "$x{$0,0.}"),
    ("Change in Montana net tax liability", "$y{$0,0.}"),
]

# Solve for minimum and maximum before-tax income and change in tax liability
# values in order to set the appropriate xrange and yrange
min_xval = inc_min
max_xval = inc_max
datarange_xvals = inc_max - inc_min
min_yval = 1e10
max_yval = -1e10
for filer_type in results_plot:
    min_yval = np.minimum(
        min_yval, filer_type[
            "Montana net tax liability change vector, dollars"
        ].min()
    )
    max_yval = np.maximum(
        max_yval, filer_type[
            "Montana net tax liability change vector, dollars"
        ].max()
    )
datarange_yvals = max_yval - min_yval
fig4_buffer_pct = 0.05
fig4 = figure(
    height=500,
    width=800,
    x_axis_label="Before-tax employment income",
    y_axis_label="Change in Montana net tax liability",
    y_range=(
        min_yval,
        max_yval + fig4_buffer_pct * datarange_yvals
    ),
    x_range=(
        min_xval,
        max_xval
    ),
    tools=[
        "save",
        "zoom_in",
        "zoom_out",
        "box_zoom",
        "pan",
        "undo",
        "redo",
        "reset",
        "hover",
        "help",
    ],
    toolbar_location="left",
)
fig4.toolbar.logo = None

l0 = fig4.line(
    x="inc_before_tax",
    y="mt_net_tax_liab_dol_chg",
    source=cds_list[0],
    color="blue",  # Category10[4][0],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l1 = fig4.line(
    x="inc_before_tax",
    y="mt_net_tax_liab_dol_chg",
    source=cds_list[1],
    color="purple",  # Category10[4][1],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l2 = fig4.line(
    x="inc_before_tax",
    y="mt_net_tax_liab_dol_chg",
    source=cds_list[2],
    color="green",  # Category10[4][2],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)
l3 = fig4.line(
    x="inc_before_tax",
    y="mt_net_tax_liab_dol_chg",
    source=cds_list[3],
    color="red",  # Category10[4][3],
    line_width=3,
    alpha=0.7,
    muted_alpha=0.15,
)

# Dashed horizontal line at $0 change
fig4.line(
    x=[min_xval - fig4_buffer_pct * datarange_xvals,
       max_xval + fig4_buffer_pct * datarange_xvals],
    y=[0.0, 0.0],
    color="black",
    line_width=2,
    line_dash="dashed",
    alpha=0.5,
)

# Add title
fig4.add_layout(
    Title(
        text=fig4_title,
        text_font_style="bold",
        text_font_size="14pt",
        align="center",
    ),
    "above",
)

# Add legend
legend = Legend(
    items=[
        (filer_type_label_list[0], [l0]),
        (filer_type_label_list[1], [l1]),
        (filer_type_label_list[2], [l2]),
        (filer_type_label_list[3], [l3]),
    ],
    # location="center",
)
fig4.add_layout(legend)
fig4.legend.location = "top_right"
fig4.legend.click_policy = "mute"

# Add the HoverTool to the figure
fig4.add_tools(
    HoverTool(
        tooltips=tooltips,
        toggleable=False,
    )
)

# # Customize the x-axis and y-axis ticks and tick lables and gridlines
# fig4.xaxis.ticker = [0, 25_000, 50_000, 75_000, 100_000, 125_000, 150_000,
#                      175_000, 200_000]
# fig4.xaxis.major_label_overrides = {
#     0: '$0', 25_000: '$25k', 50_000: '$50k', 75_000: '$75k', 100_000: '$100k',
#     125_000: '$125k', 150_000: '$150k', 175_000: '$175k', 200_000: '$200k'
# }
# fig4.yaxis.ticker = [
#     -700, -600, -500, -400, -300, -200, -100, 0, 100, 200, 300, 400
# ]
# fig4.yaxis.major_label_overrides = {
#     -700: '-$700', -600: '-$600', -500: '-$500', -400: '-$400', -300: '-$300',
#     -200: '-$200', -100: '-$100', 0: '$0', 100: '$100'
# }

# Add source text below figure
fig4.add_layout(
    Title(
        text="Source: Richard W. Evans (@RickEcon), FiscalSim open source " +
        "microsimulation model of federal and state individual tax and " +
        "benefit policy.",
        align="left",
        text_font_size="3mm",
        text_font_style="italic",
    ),
    "below",
)

show(fig4)


Loading BokehJS ...

FileNotFoundError: [Errno 2] No such file or directory: './images/NetStateTaxLiabChg.html'